# Final Experiments - Multi-label CNNText Non-problem Grid Search

## Utilities and Imports

In [1]:
%reload_ext autoreload
%autoreload 2

import itertools
import random
from collections import Counter
import numpy as np
import pickle
from operator import itemgetter
import matplotlib
from matplotlib import pyplot as plt

%matplotlib inline
# matplotlib.rcParams['figure.figsize'] = [5, 10]

from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix, f1_score
from sklearn.metrics import precision_recall_fscore_support, hamming_loss
from sklearn.svm import LinearSVC, SVC
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable

from fastai import text as ft
from fastai import dataloader as fd
from fastai import dataset as fs
from fastai import learner as fl
from fastai import core as fc
from fastai import metrics as fm


from skai.runner import TextRunner, Adam_lambda
from skai.mwrapper import MWrapper, SKModel
from skai.utils import multi_to_text_out, vote_pred
from skai.utils import get_classification_type, weights_init, multilabel_prediction, prf_report
from skai.dataset import TokenDataset, SimpleDataset
from skai.metrics import f1_micro_skai


def mapt(f, *iters):
    return tuple(map(f, *iters))

def mapl(f, *iters):
    return list(map(f, *iters))

def manually_remove_problems(data):
    """ remove problem from data if it has a certain tag"""
    final_data = {}
    remove = ['*special']
    for i in data:
        if set(data[i][1][0]).intersection(set(remove)) == set():
            if data[i][0][0] != '':
                final_data[i] = data[i]
    return final_data

def get_single_label_problems(data):
    '''returns a dict of all problems which only have one label'''
    single_label_problems = {}
    for i in data:
        if len(data[i][1][0]) == 1:
            single_label_problems[i] = data[i]
    return single_label_problems

def get_classwise_distribution(data):
    class_count = {}
    for i in data:
        for cls in data[i][1][0]:
            if cls in class_count:
                class_count[cls] +=1 
            else:
                class_count[cls] = 1
    return class_count


def get_topk_single_label_problems(data,k):
    """ get top k by frequency single label problems"""
    class_dict = get_classwise_distribution(data)
    print(class_dict)
    class_dict = dict(sorted(class_dict.items(), key=itemgetter(1), reverse=True)[:k])
    print(set(class_dict.keys()))

    topk_data = {}
    for i in data:
        if set(data[i][1][0]).intersection(set(class_dict.keys())) != set():
            topk_data[i] = data[i]
            
    return topk_data

def make_text_dataset(rdata):
    Xtext, ytext = [], []
    for url, data in rdata.items():
        try:
            ytext.append(data[1][0][0])
        except IndexError:
            continue
        Xtext.append(data[0][0])
    return Xtext, ytext

def make_multi_text_dataset(rdata):
    Xtext, ytext = [], []
    for url, data in rdata.items():
        try:
            ytext.append(data[1][0])
        except IndexError:
            continue
        Xtext.append(data[0][0])
    return Xtext, ytext

def make_statement_dataset(rdata):
    Xtext, ytext = [], []
    for url, data in rdata.items():
        try:
            ytext.append(data[1][0][0])
        except IndexError:
            continue
        Xtext.append(data[0][2])
    return Xtext, ytext

def make_non_statement_dataset(rdata):
    Xtext, ytext = [], []
    for url, data in rdata.items():
        try:
            ytext.append(data[1][0][0])
        except IndexError:
            continue
        Xtext.append(f'{data[0][3]}\n{data[0][4]}\n{data[0][5]}')
    return Xtext, ytext

def make_multi_statement_dataset(rdata):
    Xtext, ytext = [], []
    for url, data in rdata.items():
        try:
            ytext.append(data[1][0])
        except IndexError:
            continue
        Xtext.append(data[0][2])
    return Xtext, ytext

def make_multi_io_dataset(rdata):
    Xtext, ytext = [], []
    for url, data in rdata.items():
        try:
            ytext.append(data[1][0])
        except IndexError:
            continue
        Xtext.append(f'{data[0][3]}\n{data[0][4]}\n{data[0][5]}')
    return Xtext, ytext

def get_class_list(labels):
    return list(set(labels))

def plot_confusion_matrix(y_true, y_pred, classes,
                          normalize=True,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues):
    """
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    cm = confusion_matrix(y_true, y_pred, labels=classes)
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')

    print(cm)
    fig = plt.gcf()
    fig.set_size_inches(22, 16)
    plt.imshow(cm, interpolation='nearest', cmap=cmap, vmin=0.0, vmax=1.0)
#     plt.title(title, fontsize)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, fontsize=32)
    plt.yticks(tick_marks, classes, fontsize=32)

    print(cm.max())
    fmt = '.2f' if normalize else 'd'
    thresh = 0.5
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, format(cm[i, j], fmt),
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black",
                 fontsize=32)

    plt.tight_layout()
    plt.ylabel('True label', fontsize=32)
    plt.xlabel('Predicted label', fontsize=32)

/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/ensemble/weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d


## Load data

In [2]:
top10m = pickle.load(open('data/10multi_26aug.pkl', 'rb'))
top20m = pickle.load(open('data/20multi_26aug.pkl', 'rb'))

top10nm, top20nm = mapt(make_multi_io_dataset, [top10m, top20m])

In [3]:
print(len(top10nm[0]))

3737


In [4]:
print(top20nm[1][0])
print(top10nm[1][0])

['binary search', 'implementation', 'data structures']
['binary search', 'data structures', 'brute force', 'dp']


## CNN Experiments

In [5]:
class CNN_Text(nn.Module):
    def __init__(self, embed_num, class_num, kernel_sizes=[3, 4, 5],
                 kernel_num=512, embed_dim=300):
        super().__init__()
        self.kernel_num = kernel_num
        self.hparams = {'kernel_sizes': kernel_sizes,
                        'kernel_num': kernel_num,
                        'embed_dim': embed_dim}
        
        self.embed = nn.Embedding(embed_num, embed_dim)
        
        convs = [nn.Conv1d(1, kernel_num, (ks, embed_dim))
                 for ks in kernel_sizes]
        self.convs = nn.ModuleList(convs)
#         self.bn1 = nn.BatchNorm2d(kernel_num)
        self.fc1 = nn.Linear(len(kernel_sizes) * kernel_num, class_num)
    
    def conv_and_pool(self, x, conv):
        x = F.relu(conv(x)).squeeze(3)  # (N, Co, W)
        x = F.max_pool1d(x, x.size(2)).squeeze(2)
        return x
    
    def forward(self, x):
        x = self.embed(x)
        x = x.unsqueeze(1)
        
        x = [F.relu(conv(x)).squeeze(3) for conv in self.convs]
        x = [F.max_pool1d(i, i.size(2)).squeeze(2) for i in x]
        x = torch.cat(x, 1)
        
        out = torch.sigmoid(self.fc1(x))
        return out

In [6]:
def cnn_gridsearch_gen():
    all_kernel_sizes = [3, 4, 5, 10, 15]
    all_kernel_num = [128, 256, 384, 512]
    all_embed_dim = [100, 200, 300]
    
    for ks in itertools.combinations(all_kernel_sizes, 3):
        for kn in all_kernel_num:
            for ed in all_embed_dim:
                yield ks, kn, ed
    raise StopIteration

In [7]:
# ks = itertools.combinations([3, 4, 5, 10, 15], 3)
# print(list(ks))

### 20-multi

In [9]:
trunner = TextRunner([None], top20nm[0], top20nm[1], 'top20nm', make_pyt_data=False)
in_dim = len(trunner.alldata.tvectorizer.itos)
Xall, yall = [], []
for X, y in trunner.alldata:
    Xall.append(X)
    yall.append(y)
    
Xall, yall = [np.array(Xall), np.array(yall)]

Checkpoint reached: raw data cleaned.
multilabel classification.


In [33]:
runs = 1
out_dim = 20

avg_scores = []


for i, (ks, kn, ed) in enumerate(cnn_gridsearch_gen()):
    print(f'Run {i}: {ks}, {kn}, {ed}')
    
    all_preds, all_targs = [], []
    outer_cv = KFold(n_splits=10, shuffle=True, random_state=41)

    outer_cv.get_n_splits(Xall, yall)
    for j, (nontest_i, test_i) in enumerate(outer_cv.split(Xall, yall)):
        X_train, y_train = Xall[nontest_i], yall[nontest_i]
        X_test, y_test = Xall[test_i], yall[test_i]

        textcnn = MWrapper(CNN_Text(in_dim, out_dim, kernel_sizes=ks,
                                    kernel_num=kn, embed_dim=ed),
                           f'cnntext20nm_grid_{i}{j}')
        textcnn.model.apply(weights_init)

        dl_train = fd.DataLoader(SimpleDataset(X_train, y_train),
                                 batch_size=32, num_workers=2,
                                 pad_idx=1, transpose=False)
        dl_val = fd.DataLoader(SimpleDataset(X_test, y_test),
                               batch_size=32, num_workers=2,
                               pad_idx=1, transpose=False)
        modeldata = fs.ModelData(str(textcnn.path), dl_train, dl_val)
        learner = fl.Learner.from_model_data(textcnn.model,
                                             modeldata,
                                             opt_fn=Adam_lambda())
        learner.metrics = [f1_micro_skai]
        learner.fit(5e-4, 10, best_save_name='best')

        dl_test = fd.DataLoader(SimpleDataset(X_test, y_test),
                                batch_size=32, num_workers=2,
                                pad_idx=1, transpose=False)
        learner.load('best')
        preds, targs = learner.predict_dl(dl_test)
        preds = multilabel_prediction(preds, 0.5)

        all_preds.append(preds)
        all_targs.append(targs)

    avg_score = f1_score(np.concatenate(np.array(all_targs), axis=0), 
                         np.concatenate(np.array(all_preds), axis=0), average='micro')
    avg_scores.append([avg_score, textcnn.model.hparams])

Run 0: (3, 4, 5), 128, 100
Note: Model directory for cnntext20nm_grid_00 exists.
Note: Checkpoints directory for cnntext20nm_grid_00 exists.


epoch      trn_loss   val_loss   f1_micro_skai               
    0      0.10463    0.09332    0.0       
  9%|▉         | 10/112 [00:00<00:01, 99.20it/s, loss=0.101]

/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3

    1      0.090115   0.092623   0.0                          
  9%|▉         | 10/112 [00:00<00:01, 99.87it/s, loss=0.0894]

/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3

...

/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3

    1      0.083463   0.079759   0.160473                     
    2      0.07515    0.076996   0.242042                     
    3      0.066551   0.076191   0.299894                     
    4      0.057395   0.077099   0.316464                     
    5      0.047562   0.078137   0.34644                      
    6      0.037714   0.079082   0.352692                     
    7      0.02904    0.079507   0.373748                     
    8      0.023476   0.082028   0.357559                     
    9      0.020041   0.089323   0.330424                     



/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/aayn/anaconda3

epoch      trn_loss   val_loss   f1_micro_skai 
    0      0.093098   0.083134   0.0       
    1      0.084356   0.076865   0.16613                      
    2      0.076259   0.073507   0.282324                     
    3      0.068113   0.072155   0.319161                     
    4      0.059199   0.072068   0.348837                     
    5      0.049498   0.072716   0.364082                     
    6      0.039545   0.073875   0.369807                     
    7      0.030488   0.076713   0.375679                     
    8      0.024213   0.083409   0.389414                     
    9      0.022446   0.080107   0.35425                      



/home/aayn/anaconda3/envs/fastai/lib/python3.6/site-packages/ipykernel_launcher.py:7: DeprecationWarning: generator 'cnn_gridsearch_gen' raised StopIteration
  import sys


In [35]:
print(avg_scores)

[[0.2820037105751391, {'kernel_sizes': (3, 4, 5), 'kernel_num': 128, 'embed_dim': 100}], [0.3121485772704038, {'kernel_sizes': (3, 4, 5), 'kernel_num': 128, 'embed_dim': 200}], [0.3231970754403456, {'kernel_sizes': (3, 4, 5), 'kernel_num': 128, 'embed_dim': 300}], [0.3014507862045, {'kernel_sizes': (3, 4, 5), 'kernel_num': 256, 'embed_dim': 100}], [0.33308745184820915, {'kernel_sizes': (3, 4, 5), 'kernel_num': 256, 'embed_dim': 200}], [0.3408926997355558, {'kernel_sizes': (3, 4, 5), 'kernel_num': 256, 'embed_dim': 300}], [0.31352459016393447, {'kernel_sizes': (3, 4, 5), 'kernel_num': 384, 'embed_dim': 100}], [0.33879254977520884, {'kernel_sizes': (3, 4, 5), 'kernel_num': 384, 'embed_dim': 200}], [0.3380618425247051, {'kernel_sizes': (3, 4, 5), 'kernel_num': 384, 'embed_dim': 300}], [0.32173397680128696, {'kernel_sizes': (3, 4, 5), 'kernel_num': 512, 'embed_dim': 100}], [0.3395952592114811, {'kernel_sizes': (3, 4, 5), 'kernel_num': 512, 'embed_dim': 200}], [0.3517198636504493, {'kernel_

In [34]:
best_model_params = max(avg_scores, key=lambda x: x[0])
print(best_model_params)

[0.3729184925503944, {'kernel_sizes': (3, 10, 15), 'kernel_num': 512, 'embed_dim': 300}]
